# msticpy Threat Intel Lookup
This notebook describes the use of the Threat Intelligence lookup class in msticpy.
The class allows lookup of individual or multiple IoCs from one or more TI providers.

TILookup is also extensible - you can subclass TIProvider to implement your own custom lookups. You can also subclass the HTTPProvider or KqlProvider classes, which provide support for querying a REST endpoint or Log Analytics table respectively.

<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#msticpy-Threat-Intel-Lookup" data-toc-modified-id="msticpy-Threat-Intel-Lookup-1">msticpy Threat Intel Lookup</a></span></li><li><span><a href="#TILookup-class" data-toc-modified-id="TILookup-class-2">TILookup class</a></span><ul class="toc-item"><li><span><a href="#Available-Providers" data-toc-modified-id="Available-Providers-2.1">Available Providers</a></span></li><li><span><a href="#Configuration-File" data-toc-modified-id="Configuration-File-2.2">Configuration File</a></span></li><li><span><a href="#Looking-up-IoCs" data-toc-modified-id="Looking-up-IoCs-2.3">Looking up IoCs</a></span><ul class="toc-item"><li><span><a href="#lookup_ioc" data-toc-modified-id="lookup_ioc-2.3.1">lookup_ioc</a></span></li><li><span><a href="#Lookup-an-IoC-from-a-single-provider" data-toc-modified-id="Lookup-an-IoC-from-a-single-provider-2.3.2">Lookup an IoC from a single provider</a></span><ul class="toc-item"><li><span><a href="#Or-convert-result-to-a-DataFrame-and-let-pandas-do-the-display-work..." data-toc-modified-id="Or-convert-result-to-a-DataFrame-and-let-pandas-do-the-display-work...-2.3.2.1">Or convert result to a DataFrame and let pandas do the display work...</a></span></li></ul></li></ul></li><li><span><a href="#Lookup-using-all-primary-providers" data-toc-modified-id="Lookup-using-all-primary-providers-2.4">Lookup using all primary providers</a></span></li><li><span><a href="#Provider-Usage" data-toc-modified-id="Provider-Usage-2.5">Provider Usage</a></span><ul class="toc-item"><li><span><a href="#Use-to-do-a-passive-DNS-lookup" data-toc-modified-id="Use-to-do-a-passive-DNS-lookup-2.5.1">Use to do a passive DNS lookup</a></span></li><li><span><a href="#Use-to-do-a-GeoIP-lookup" data-toc-modified-id="Use-to-do-a-GeoIP-lookup-2.5.2">Use to do a GeoIP lookup</a></span></li></ul></li><li><span><a href="#Inferring-IoC-Type-vs.-Specifying-explicity" data-toc-modified-id="Inferring-IoC-Type-vs.-Specifying-explicity-2.6">Inferring IoC Type vs. Specifying explicity</a></span></li><li><span><a href="#Looking-up-Multiple-IoCs" data-toc-modified-id="Looking-up-Multiple-IoCs-2.7">Looking up Multiple IoCs</a></span><ul class="toc-item"><li><span><a href="#lookup_iocs" data-toc-modified-id="lookup_iocs-2.7.1">lookup_iocs</a></span></li><li><span><a href="#Multiple-IP-Lookup-from-single-provider" data-toc-modified-id="Multiple-IP-Lookup-from-single-provider-2.7.2">Multiple IP Lookup from single provider</a></span></li><li><span><a href="#Multiple-IoCs-using-all-providers" data-toc-modified-id="Multiple-IoCs-using-all-providers-2.7.3">Multiple IoCs using all providers</a></span></li><li><span><a href="#Multiple-Mixed-IoC-Types" data-toc-modified-id="Multiple-Mixed-IoC-Types-2.7.4">Multiple Mixed IoC Types</a></span></li></ul></li><li><span><a href="#Specifying-Time-Ranges" data-toc-modified-id="Specifying-Time-Ranges-2.8">Specifying Time Ranges</a></span></li></ul></li></ul></div>

In [1]:
# Imports
import sys
import warnings

from msticpy.common.utility import check_py_version
MIN_REQ_PYTHON = (3,6)
check_py_version(MIN_REQ_PYTHON)

from msticpy import init_notebook
init_notebook(namespace=globals());


Processing imports....
Checking configuration....

The following configuration errors were found: 
 -----------------------------------------------
TIProviders/AzureSentinel: Missing or invalid WorkspaceID.
TIProviders/AzureSentinel: Missing or invalid TenantID.

The following configuration warnings were found: 
 -------------------------------------------------
No AzureCLI section in settings.
Setting options....


# TILookup class
Input can be a single IoC observable or a pandas DataFrame containing
multiple observables. Processing may require a an API key and
processing performance may be limited to a specific number of
requests per minute for the account type that you have.

In [2]:
# TILookup class
display(Markdown("### Constructor\n"))
print(TILookup.__init__.__doc__)
display(Markdown("### Attributes\n"))
for name in [att for att in dir(TILookup) if not att.startswith("_")]:
    display(Markdown(f"#### _{name}()_"))
    print(getattr(TILookup, name).__doc__)
    print()

### Constructor



        Initialize TILookup instance.

        Parameters
        ----------
        primary_providers : Optional[List[TIProvider]], optional
            Primary TI Providers, by default None
        secondary_providers : Optional[List[TIProvider]], optional
            Secondary TI Providers, by default None
        providers: Optional[List[str]], optional
            List of provider names to load, by default all available
            providers are loaded. To see the list of available providers
            call `TILookup.list_available_providers()`.
            Note: if primary_provides or secondary_providers is specified
            This will override the providers list.

        


### Attributes


#### _add_provider()_


        Add a TI provider to the current collection.

        Parameters
        ----------
        provider : TIProvider
            Provider instance
        name : str, optional
            The name to use for the provider (overrides the class name
            of `provider`)
        primary : bool, optional
            "primary" or "secondary" if False, by default "primary"

        



...

Reload provider settings from config.



#### _reload_providers()_


        Reload providers based on currrent settings in config.

        Parameters
        ----------
        clear_keyring : bool, optional
            Clears any secrets cached in keyring, by default False

        



#### _result_to_df()_


        Return DataFrame representation of IoC Lookup response.

        Parameters
        ----------
        ioc_lookup : Tuple[bool, List[Tuple[str, LookupResult]]]
            Output from `lookup_ioc`

        Returns
        -------
        pd.DataFrame
            The response as a DataFrame with a row for each
            provider response.

        



## Available Providers
The **msticpy** TI Provider library can lookup IoCs in multiple providers.

The list below shows the current set of providers.

In [3]:
TILookup.list_available_providers()

AzSTI
OPR
OTX
Tor
VirusTotal
XForce


You can view the list of supported query types for each provider with the `show_query_types=True` parameter

In [4]:
TILookup.list_available_providers(show_query_types=True)

AzSTI
Azure Sentinel TI provider class. Supported query types:
	ioc_type=dns
	ioc_type=file_hash
	ioc_type=hostname
	ioc_type=ipv4
	ioc_type=ipv6
	ioc_type=linux_path
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_type=url
	ioc_type=windows_path
OPR
Open PageRank Lookup. Supported query types:
	ioc_type=dns
OTX
AlientVault OTX Lookup. Supported query types:
	ioc_type=dns
	ioc_type=dns, ioc_query_type=geo
	ioc_type=dns, ioc_query_type=passivedns
	ioc_type=file_hash
	ioc_type=hostname
	ioc_type=ipv4
	ioc_type=ipv4, ioc_query_type=geo
	ioc_type=ipv4, ioc_query_type=passivedns
	ioc_type=ipv6
	ioc_type=ipv6, ioc_query_type=geo
	ioc_type=ipv6, ioc_query_type=passivedns
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_type=url
Tor
Tor Exit Nodes Lookup. Supported query types:
	ioc_type=ipv4
VirusTotal
VirusTotal Lookup. Supported query types:
	ioc_type=dns
	ioc_type=file_hash
	ioc_type=ipv4
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_t

## Loading TIProviders

Calling TILookup with no parameters will load all of the available providers
that have a configuration entry in `msticpyconfig.yaml` (see next section)

In [5]:
# load all configured providers
ti_lookup = TILookup()
ti_lookup.provider_status

# Restricting which providers get loaded
#ti_lookup = TILookup(providers=["VirusTotal", "XForce"])

Please wait. Loading Kqlmagic extension...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Using Open PageRank. See https://www.domcop.com/openpagerank/what-is-openpagerank


['OTX - AlientVault OTX Lookup. (primary)',
 'OPR - Open PageRank Lookup. (primary)',
 'Tor - Tor Exit Nodes Lookup. (primary)',
 'VirusTotal - VirusTotal Lookup. (primary)',
 'XForce - IBM XForce Lookup. (primary)',
 'AzSTI - Azure Sentinel TI provider class. (secondary)']

## Configuration File
You can configure primary and secondary providers. 
Primary providers are used by default.

You may need to supply an authorization (API) key and in some cases a user ID for each provider.

For LogAnalytics/Azure Sentinel providers, you will need the workspace ID and tenant ID and will need to authenticate in order to access the data (although if you have an existing authenticated connection with the same workspace/tenant, this connection will be re-used).

The configuration file is read from the current directory.

Alternatively, you can specify a location for this file in an environment variable `MSTICPYCONFIG`.

If you need to create a config file, uncomment the lines in the following cell.<br>
### <font color="red">Warning - this will overwrite a file of the same name in the current directory</font>

Delete any provider entries that you do not want to use and add the missing parameters for your providers. 

In [6]:
# %%writefile msticpyconfig.yaml
# QueryDefinitions:

# TIProviders:
#   OTX:
#     Args:
#       AuthKey: "your-otx-key"
#     Primary: True
#     Provider: "OTX" # Explicitly name provider to override
#   VirusTotal:
#     Args:
#       AuthKey: "your-vt-key"
#     Primary: True
#     Provider: "VirusTotal"
#   XForce:
#     Args:
#       ApiID: "your-xforce-id"
#       AuthKey: "your-xforce-key"
#     Primary: True
#     Provider: "XForce"
#   AzureSentinel:
#     # Note if you do not specify any settings in the Args key for the AzureSentinel
#     # provider, it will default to using your default Azure Sentinel workspace.
#     Args:
#       WorkspaceID: "your-azure-sentinel-workspace-id"
#       TenantID: "your-azure-sentinel-tenant-id"
#     Primary: True
#     Provider: "AzSTI"

Reload providers to pick up new settings

In [7]:
ti_lookup.reload_providers()
ti_lookup.provider_status

Settings reloaded. Use reload_providers to update settings for loaded providers.


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Using Open PageRank. See https://www.domcop.com/openpagerank/what-is-openpagerank


['OTX - AlientVault OTX Lookup. (primary)',
 'OPR - Open PageRank Lookup. (primary)',
 'Tor - Tor Exit Nodes Lookup. (primary)',
 'VirusTotal - VirusTotal Lookup. (primary)',
 'XForce - IBM XForce Lookup. (primary)',
 'AzSTI - Azure Sentinel TI provider class. (secondary)']

## Looking up IoCs

### lookup_ioc
To lookup a single IoC.
```
ti_lookup.lookup_ioc(
    observable: str = None,
    ioc_type: str = None,
    ioc_query_type: str = None,
    providers: List[str] = None,
    prov_scope: str = 'primary',
    **kwargs,
) -> Tuple[bool, List[Tuple[str, msticpy.sectools.tiproviders.ti_provider_base.LookupResult]]]

Lookup single IoC in active providers.

Parameters
----------
observable : str
    IoC observable
    (`ioc` is also an alias for observable)
ioc_type : str, optional
    One of IoCExtract.IoCType, by default None
    If none, the IoC type will be inferred
ioc_query_type: str, optional
    The ioc query type (e.g. rep, info, malware)
providers: List[str]
    Explicit list of providers to use
prov_scope : str, optional
    Use primary, secondary or all providers, by default "primary"
kwargs :
    Additional arguments passed to the underlying provider(s)

Returns
-------
Tuple[bool, List[Tuple[str, LookupResult]]]
    The result returned as a tuple(bool, list):
    bool indicates whether a TI record was found in any provider
    list has an entry for each provider result
```

In [8]:
# Uncomment this and run to see the document string
# ti_lookup.lookup_ioc?

### Lookup an IoC from a single provider
And show the output

In [9]:
result = ti_lookup.lookup_ioc(observable="52.183.120.194", providers=["AzSTI", "XForce"])
ti_lookup.result_to_df(result)

<IPython.core.display.Javascript object>

Ioc IocType QuerySubtype Provider Result     Severity  \
XForce  52.183.120.194    ipv4         None   XForce   True      warning   
AzSTI   52.183.120.194    ipv4         None    AzSTI  False  information   

                                                                                                    Details  \
XForce  {'score': 1, 'cats': {}, 'categoryDescriptions': {}, 'reason': 'Regional Internet Registry', 're...   
AzSTI                                                                                            Not found.   

                                                                                                  RawResult  \
XForce  {'ip': '52.183.120.194', 'history': [{'created': '2012-03-22T07:26:00.000Z', 'reason': 'Regional...   
AzSTI                                                                                                  None   

                                                 Reference Status  
XForce  https://api.xforce.ibmcloud.com/ipr/52.183.120.194      0  
AzSTI                                                 None      0

In [10]:
result = ti_lookup.lookup_ioc(observable="52.183.120.194")
ti_lookup.result_to_df(result).T

OTX  \
Ioc                                                                                                52.183.120.194   
IocType                                                                                                      ipv4   
QuerySubtype                                                                                                 None   
Provider                                                                                                      OTX   
Result                                                                                                       True   
Severity                                                                                              information   
Details       {'pulse_count': 0, 'sections_available': ['general', 'geo', 'reputation', 'url_list', 'passive_d...   
RawResult     {'sections': ['general', 'geo', 'reputation', 'url_list', 'passive_dns', 'malware', 'nids_list',...   
Reference                                https://otx.alienvault.com/api/v1/indicators/IPv4/52.183.120.194/general   
Status                                                                                                          0   

                                       OPR  \
Ioc                         52.183.120.194   
IocType                               ipv4   
QuerySubtype                          None   
Provider                               OPR   
Result                               False   
Severity                       information   
Details       IoC type ipv4 not supported.   
RawResult                             None   
Reference                             None   
Status                                   1   

                                                      Tor  \
Ioc                                        52.183.120.194   
IocType                                              ipv4   
QuerySubtype                                         None   
Provider                                              Tor   
Result                                               True   
Severity                                      information   
Details                                        Not found.   
RawResult                                            None   
Reference     https://check.torproject.org/exit-addresses   
Status                                                  0   

                                                                                                       VirusTotal  \
Ioc                                                                                                52.183.120.194   
IocType                                                                                                      ipv4   
QuerySubtype                                                                                                 None   
Provider                                                                                               VirusTotal   
Result                                                                                                       True   
Severity                                                                                              information   
Details         {'verbose_msg': 'IP address in dataset', 'response_code': 1, 'detected_urls': [], 'positives': 0}   
RawResult     {'https_certificate_date': 1569589456, 'whois': 'NetRange: 52.145.0.0 - 52.191.255.255
CIDR: 52....   
Reference                                                   https://www.virustotal.com/vtapi/v2/ip-address/report   
Status                                                                                                          0   

                                                                                                           XForce  
Ioc                                                                                                52.183.120.194  
IocType                                                                                                      ipv4  
QuerySu

In [11]:
import pprint
pp = pprint.PrettyPrinter(indent=2)

result, details = ti_lookup.lookup_ioc(observable="38.75.137.9", providers=["OTX"])

# the details is a list (since there could be multiple responses for an IoC)
for provider, detail in details:
    print(provider)
    detail.summary
# Un-comment to view raw response
#     print("\nRaw Results")
#     pp.pprint(detail.raw_result)


OTX
ioc: 38.75.137.9 ( ipv4 )
result: True
{   'names': ['Underminer.EK - Exploit Kit IOC Feed', 'Underminer EK'],
    'pulse_count': 2,
    'references': [   [],
                      [   'https://blog.malwarebytes.com/threat-analysis/2019/07/exploit-kits-summer-2019-review/']],
    'tags': [['Underminer.EK'], []]}
reference:  https://otx.alienvault.com/api/v1/indicators/IPv4/38.75.137.9/general


#### Or convert result to a DataFrame and let pandas do the display work...

In [12]:
result = ti_lookup.lookup_ioc(observable="38.75.137.9", providers=["OTX"])
ti_lookup.result_to_df(result).T

OTX
Ioc                                                                                                   38.75.137.9
IocType                                                                                                      ipv4
QuerySubtype                                                                                                 None
Provider                                                                                                      OTX
Result                                                                                                       True
Severity                                                                                                     high
Details       {'pulse_count': 2, 'names': ['Underminer.EK - Exploit Kit IOC Feed', 'Underminer EK'], 'tags': [...
RawResult     {'sections': ['general', 'geo', 'reputation', 'url_list', 'passive_dns', 'malware', 'nids_list',...
Reference                                   https://otx.alienvault.com/api/v1/indicators/IPv4/38.75.137.9/general
Status                                                                                                          0

In [13]:
# Extract a single field (RawResult) from the dataframe (.iloc[0] is to select the row)
ti_lookup.result_to_df(result)["RawResult"].iloc[0]

{'sections': ['general',
  'geo',
  'reputation',
  'url_list',
  'passive_dns',
  'malware',
  'nids_list',
  'http_scans'],
 'city': 'Los Angeles',
 'area_code': 0,
 'accuracy_radius': 1000,
 'pulse_info': {'count': 2,
  'references': ['https://blog.malwarebytes.com/threat-analysis/2019/07/exploit-kits-summer-2019-review/'],
  'pulses': [{'indicator_type_counts': {'domain': 1, 'hostname': 1, 'IPv4': 7},
    'pulse_source': 'api',
    'TLP': 'white',
    'description': 'IPs and hostnames for the Exploit Kit known as Underminer.EK.',
    'subscriber_count': 257,
    'tags': ['Underminer.EK'],
    'export_count': 1,
    'malware_families': [],
    'is_modified': True,
    'upvotes_count': 0,
    'modified_text': '248 days ago ',
    'is_subscribing': None,
    'references': [],
    'targeted_countries': [],
    'groups': [],
    'vote': 0,
    'validator_count': 0,
    'threat_hunter_scannable': True,
    'is_author': False,
    'adversary': '',
    'id': '5db816cba3e59aeced1fad16',
   

## Lookup using all primary providers

In [14]:
result = ti_lookup.lookup_ioc(observable="188.127.231.124")
ti_lookup.result_to_df(result)

Ioc IocType QuerySubtype    Provider Result  \
OTX         188.127.231.124    ipv4         None         OTX   True   
OPR         188.127.231.124    ipv4         None         OPR  False   
Tor         188.127.231.124    ipv4         None         Tor   True   
VirusTotal  188.127.231.124    ipv4         None  VirusTotal   True   
XForce      188.127.231.124    ipv4         None      XForce   True   

               Severity  \
OTX                high   
OPR         information   
Tor         information   
VirusTotal  information   
XForce          warning   

                                                                                                        Details  \
OTX         {'pulse_count': 4, 'names': ['Locky Ransomware C2 IP blocklist (LY_C2_IPBL)', 'Malicious IP', 'F...   
OPR                                                                                IoC type ipv4 not supported.   
Tor                                                                                                  Not found.   
VirusTotal  {'verbose_msg': 'IP address in dataset', 'response_code': 1, 'detected_urls': [], 'positives': 0...   
XForce      {'score': 1, 'cats': {}, 'categoryDescriptions': {}, 'reason': 'Regional Internet Registry', 're...   

                                                                                                      RawResult  \
OTX         {'sections': ['general', 'geo', 'reputation', 'url_list', 'passive_dns', 'malware', 'nids_list',...   
OPR                                                                                                        None   
Tor                                                                                                        None   
VirusTotal  {'undetected_downloaded_samples': [{'date': '2018-01-09 20:05:03', 'positives': 0, 'total': 71, ...   
XForce      {'ip': '188.127.231.124', 'history': [{'created': '2012-03-22T07:26:00.000Z', 'reason': 'Regiona...   

                                                                            Reference  \
OTX         https://otx.alienvault.com/api/v1/indicators/IPv4/188.127.231.124/general   
OPR                                                                              None   
Tor                                       https://check.torproject.org/exit-addresses   
VirusTotal                      https://www.virustotal.com/vtapi/v2/ip-address/report   
XForce                            https://api.xforce.ibmcloud.com/ipr/188.127.231.124   

           Status  
OTX             0  
OPR             1  
Tor             0  
VirusTotal      0  
XForce          0

## Provider Usage
This shows the supported IoC Types.

In some cases an IoC type will also support special types of sub-query such as geo-ip and passive-dns

In [15]:
display(ti_lookup.provider_status)
ti_lookup.loaded_providers["AzSTI"].usage()

['OTX - AlientVault OTX Lookup. (primary)',
 'OPR - Open PageRank Lookup. (primary)',
 'Tor - Tor Exit Nodes Lookup. (primary)',
 'VirusTotal - VirusTotal Lookup. (primary)',
 'XForce - IBM XForce Lookup. (primary)',
 'AzSTI - Azure Sentinel TI provider class. (secondary)']

Azure Sentinel TI provider class. Supported query types:
	ioc_type=dns
	ioc_type=file_hash
	ioc_type=hostname
	ioc_type=ipv4
	ioc_type=ipv6
	ioc_type=linux_path
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_type=url
	ioc_type=windows_path


In [16]:
ti_lookup.provider_usage()

Primary providers
-----------------

Provider class: OTX
AlientVault OTX Lookup. Supported query types:
	ioc_type=dns
	ioc_type=dns, ioc_query_type=geo
	ioc_type=dns, ioc_query_type=passivedns
	ioc_type=file_hash
	ioc_type=hostname
	ioc_type=ipv4
	ioc_type=ipv4, ioc_query_type=geo
	ioc_type=ipv4, ioc_query_type=passivedns
	ioc_type=ipv6
	ioc_type=ipv6, ioc_query_type=geo
	ioc_type=ipv6, ioc_query_type=passivedns
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_type=url

Provider class: OPR
Open PageRank Lookup. Supported query types:
	ioc_type=dns

Provider class: Tor
Tor Exit Nodes Lookup. Supported query types:
	ioc_type=ipv4

Provider class: VirusTotal
VirusTotal Lookup. Supported query types:
	ioc_type=dns
	ioc_type=file_hash
	ioc_type=ipv4
	ioc_type=md5_hash
	ioc_type=sha1_hash
	ioc_type=sha256_hash
	ioc_type=url

Provider class: XForce
IBM XForce Lookup. Supported query types:
	ioc_type=dns
	ioc_type=dns, ioc_query_type=malware
	ioc_type=dns, ioc_query_type=passi

### Use to do a passive DNS lookup

In [17]:
result = ti_lookup.lookup_ioc(observable="38.75.137.9", ico_type="ipv4", ioc_query_type="passivedns", providers=["XForce"])
print(result)
print("\nProvider result:")
result[1][0][1].raw_result

(True, [('XForce', LookupResult(ioc='38.75.137.9', ioc_type='ipv4', safe_ioc='38.75.137.9', query_subtype='passivedns', provider='XForce', result=True, severity='information', details={'records': 1}, raw_result={'Passive': {'query': '0x00000000000000000000ffff264b8909', 'records': []}, 'RDNS': ['9-137-75-38.clients.gthost.com'], 'total_rows': 1}, reference='https://api.xforce.ibmcloud.com/resolve/38.75.137.9', status=0))])

Provider result:


{'Passive': {'query': '0x00000000000000000000ffff264b8909', 'records': []},
 'RDNS': ['9-137-75-38.clients.gthost.com'],
 'total_rows': 1}

### Use to do a GeoIP lookup

In [18]:
result = ti_lookup.lookup_ioc(observable="38.75.137.9", ico_type="ipv4", ioc_query_type="geo", providers=["OTX"])
print(result)
print("\nProvider result:")
result[1][0][1].raw_result

(True, [('OTX', LookupResult(ioc='38.75.137.9', ioc_type='ipv4', safe_ioc='38.75.137.9', query_subtype='geo', provider='OTX', result=True, severity='information', details={}, raw_result={'city_data': True, 'accuracy_radius': 1000, 'area_code': 0, 'continent_code': 'NA', 'country_name': 'United States of America', 'postal_code': '90017', 'dma_code': 803, 'country_code': 'US', 'flag_url': '/assets/images/flags/us.png', 'asn': 'AS63023 AS-GLOBALTELEHOST', 'city': 'Los Angeles', 'subdivision': 'CA', 'region': 'CA', 'charset': 0, 'longitude': -118.278, 'country_code3': 'USA', 'country_code2': 'US', 'latitude': 34.0584, 'flag_title': 'United States of America'}, reference='https://otx.alienvault.com/api/v1/indicators/IPv4/38.75.137.9/geo', status=0))])

Provider result:


{'city_data': True,
 'accuracy_radius': 1000,
 'area_code': 0,
 'continent_code': 'NA',
 'country_name': 'United States of America',
 'postal_code': '90017',
 'dma_code': 803,
 'country_code': 'US',
 'flag_url': '/assets/images/flags/us.png',
 'asn': 'AS63023 AS-GLOBALTELEHOST',
 'city': 'Los Angeles',
 'subdivision': 'CA',
 'region': 'CA',
 'charset': 0,
 'longitude': -118.278,
 'country_code3': 'USA',
 'country_code2': 'US',
 'latitude': 34.0584,
 'flag_title': 'United States of America'}

## Inferring IoC Type vs. Specifying explicity
If you do a lookup without specifying a type, TILookup will try to infer the type by matching regexes. There are patterns for all supported types but there are some caveats:

- The match is not 100% foolproof - e.g. some URLs and hash types may be misidentified.
- The inference adds an overhead to each lookup.

If you know the type that you want to look up, it is always better to explicitly include it.
- For single IoC lookup, use the `ioc_type` parameter.
- For multiple IoC lookups (see below), supply either:
  - a DataFrame with a column that specifies the type for each entry
  - a dictionary of the form `{ioc_observable: ioc_type}`

## Looking up Multiple IoCs

### lookup_iocs
```
Signature:
ti_lookup.lookup_iocs(
    data: Union[pandas.core.frame.DataFrame, Mapping[str, str], Iterable[str]],
    obs_col: str = None,
    ioc_type_col: str = None,
    ioc_query_type: str = None,
    providers: List[str] = None,
    prov_scope: str = 'primary',
    **kwargs,
) -> pandas.core.frame.DataFrame

Lookup a collection of IoCs.

Parameters
----------
data : Union[pd.DataFrame, Mapping[str, str], Iterable[str]]
    Data input in one of three formats:
    1. Pandas dataframe (you must supply the column name in
    `obs_col` parameter)
    2. Mapping (e.g. a dict) of [observable, IoCType]
    3. Iterable of observables - IoCTypes will be inferred
obs_col : str, optional
    DataFrame column to use for observables, by default None
ioc_type_col : str, optional
    DataFrame column to use for IoCTypes, by default None
ioc_query_type: str, optional
    The ioc query type (e.g. rep, info, malware)
providers: List[str]
    Explicit list of providers to use
prov_scope : str, optional
    Use primary, secondary or all providers, by default "primary"
kwargs :
    Additional arguments passed to the underlying provider(s)

Returns
-------
pd.DataFrame
    DataFrame of results
```

In [19]:
# Uncomment this and run to see the document string
# ti_lookup.lookup_iocs?

### Multiple IP Lookup from single provider

In [20]:

ioc_ips = [
    "51.75.29.61",
    "33.44.55.66"
    "52.183.120.194",
    "13.91.229.209",
    "1.2.3.4",
    "52.167.223.49",
    "1.2.3.5",
]

ti_lookup.lookup_iocs(data=ioc_ips, providers="AzSTI")

<IPython.core.display.Javascript object>

Ioc IocType QuerySubtype  \
0    51.75.29.61    ipv4         None   
1  13.91.229.209    ipv4         None   
2  52.167.223.49    ipv4         None   
3        1.2.3.4    ipv4         None   
4        1.2.3.5    ipv4         None   

                                                                                             Reference  \
0   ThreatIntelligenceIndicator  | where TimeGenerated >= datetime(2020-06-09T22:21:31.328494Z) | w...   
1   ThreatIntelligenceIndicator  | where TimeGenerated >= datetime(2020-06-09T22:21:31.328494Z) | w...   
2   ThreatIntelligenceIndicator  | where TimeGenerated >= datetime(2020-06-09T22:21:31.328494Z) | w...   
3   ThreatIntelligenceIndicator  | where TimeGenerated >= datetime(2020-06-09T22:21:31.328494Z) | w...   
4   ThreatIntelligenceIndicator  | where TimeGenerated >= datetime(2020-06-09T22:21:31.328494Z) | w...   

   Result     Details  Status  Severity Provider  
0   False  Not found.       0         0    AzSTI  
1   False  Not found.       0         0    AzSTI  
2   False  Not found.       0         0    AzSTI  
3   False  Not found.       0         0    AzSTI  
4   False  Not found.       0         0    AzSTI

### Multiple IoCs using all providers
Output sorted by IoC

Note that these URLs were picked randomly from the TI databases of the three providers used. In most cases the IoC is found by only that provider, which 

In [21]:
ioc_urls = [
    "http://cheapshirts.us/zVnMrG.php",
    "http://chinasymbolic.com/i9jnrc",
    "https://hotel-bristol.lu/dlry/MAnJIPnY/",
    "http://businesstobuy.net",
    "http://append.pl/srh9xsz",
    "http://104.248.196.145/apache2",
    "http://ajaraheritage.ge/g7cberv",
    "http://cic-integration.com/hjy93JNBasdas",
    "https://google.com",  # benign
    "https://microsoft.com",  # benign
    "https://python.org",  # benign
]
results = ti_lookup.lookup_iocs(data=ioc_urls)
results.sort_values("Ioc")

Ioc IocType  \
5             http://104.248.196.145/apache2     url   
5             http://104.248.196.145/apache2     url   
5             http://104.248.196.145/apache2     url   
6            http://ajaraheritage.ge/g7cberv     url   
6            http://ajaraheritage.ge/g7cberv     url   
6            http://ajaraheritage.ge/g7cberv     url   
4                   http://append.pl/srh9xsz     url   
4                   http://append.pl/srh9xsz     url   
4                   http://append.pl/srh9xsz     url   
3                   http://businesstobuy.net     url   
3                   http://businesstobuy.net     url   
3                   http://businesstobuy.net     url   
0           http://cheapshirts.us/zVnMrG.php     url   
0           http://cheapshirts.us/zVnMrG.php     url   
0           http://cheapshirts.us/zVnMrG.php     url   
1            http://chinasymbolic.com/i9jnrc     url   
1            http://chinasymbolic.com/i9jnrc     url   
1            http://chinasymbolic.com/i9jnrc     url   
7   http://cic-integration.com/hjy93JNBasdas     url   
7   http://cic-integration.com/hjy93JNBasdas     url   
7   http://cic-integration.com/hjy93JNBasdas     url   
8                         https://google.com     url   
8                         https://google.com     url   
8                         https://google.com     url   
2    https://hotel-bristol.lu/dlry/MAnJIPnY/     url   
2    https://hotel-bristol.lu/dlry/MAnJIPnY/     url   
2    https://hotel-bristol.lu/dlry/MAnJIPnY/     url   
9                      https://microsoft.com     url   
9                      https://microsoft.com     url   
9                      https://microsoft.com     url   
10                        https://python.org     url   
10                        https://python.org     url   
10                        https://python.org     url   

                                                SafeIoc QuerySubtype  \
5                        http://104.248.196.145/apache2         None   
5                        http://104.248.196.145/apache2         None   
5                http%3A%2F%2F104.248.196.145%2Fapache2         None   
6                       http://ajaraheritage.ge/g7cberv         None   
6               http%3A%2F%2Fajaraheritage.ge%2Fg7cberv         None   
6                       http://ajaraheritage.ge/g7cberv         None   
4                      http%3A%2F%2Fappend.pl%2Fsrh9xsz         None   
4                              http://append.pl/srh9xsz         None   
4                              http://append.pl/srh9xsz         None   
3                        http%3A%2F%2Fbusinesstobuy.net         None   
3                              http://businesstobuy.net         None   
3                              http://businesstobuy.net         None   
0                      http://cheapshirts.us/zVnMrG.php         None   
0              http%3A%2F%2Fcheapshirts.us%2FzVnMrG.php         None   
0                      http://cheapshirts.us/zVnMrG.php         None   
1                       http://chinasymbolic.com/i9jnrc         None   
1               http%3A%2F%2Fchinasymbolic.com%2Fi9jnrc         None   
1                       http://chinasymbolic.com/i9jnrc         None   
7              http://cic-integration.com/hjy93JNBasdas         None   
7      http%3A%2F%2Fcic-integration.com%2Fhjy93JNBasdas         None   
7              http://cic-integration.com/hjy93JNBasdas         None   
8                                    https://google.com         None   
8                              https%3A%2F%2Fgoogle.com         None   
8                                    https://google.com         None   
2               https://hotel-bristol.lu/dlry/MAnJIPnY/         None   
2               https://hotel-bristol.lu/dlry/MAnJIPnY/         None   
2   https%3A%2F%2Fhotel-bristol.lu%2Fdlry%2FMAnJIPnY%2F         None   
9                                 https://microsoft.com         None   
9                           https%3A%2F%2Fmicros

### Multiple Mixed IoC Types

In [22]:
ioc_mixed = [
    "http://104.248.196.145/apache2",
    "http://ajaraheritage.ge/g7cberv",
    "http://cic-integration.com/hjy93JNBasdas",
    "51.75.29.61",
    "33.44.55.66",
    "52.183.120.194",
    "f8a7135496fd6168df5f0ea21c745db89ecea9accc29c5cf281cdf3145865092",
    "cc2db822f652ca67038ba7cca8a8bde3",
    "ajaraheritage.ge",
]
results = ti_lookup.lookup_iocs(data=ioc_mixed)
results

Ioc  \
0                                    http://104.248.196.145/apache2   
1                                   http://ajaraheritage.ge/g7cberv   
2                          http://cic-integration.com/hjy93JNBasdas   
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
6  f8a7135496fd6168df5f0ea21c745db89ecea9accc29c5cf281cdf3145865092   
7                                  cc2db822f652ca67038ba7cca8a8bde3   
8                                                  ajaraheritage.ge   
0                                                  ajaraheritage.ge   
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
0                                    http://104.248.196.145/apache2   
1                                   http://ajaraheritage.ge/g7cberv   
2                          http://cic-integration.com/hjy93JNBasdas   
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
6  f8a7135496fd6168df5f0ea21c745db89ecea9accc29c5cf281cdf3145865092   
7                                  cc2db822f652ca67038ba7cca8a8bde3   
8                                                  ajaraheritage.ge   
0                                    http://104.248.196.145/apache2   
1                                   http://ajaraheritage.ge/g7cberv   
2                          http://cic-integration.com/hjy93JNBasdas   
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
6  f8a7135496fd6168df5f0ea21c745db89ecea9accc29c5cf281cdf3145865092   
7                                  cc2db822f652ca67038ba7cca8a8bde3   
8                                                  ajaraheritage.ge   

       IocType  \
0          url   
1          url   
2          url   
3         ipv4   
4         ipv4   
5         ipv4   
6  sha256_hash   
7     md5_hash   
8          dns   
0          dns   
3         ipv4   
4         ipv4   
5         ipv4   
0          url   
1          url   
2          url   
3         ipv4   
4         ipv4   
5         ipv4   
6  sha256_hash   
7     md5_hash   
8          dns   
0          url   
1          url   
2          url   
3         ipv4   
4         ipv4   
5         ipv4   
6  sha256_hash   
7     md5_hash   
8          dns   

                                                            SafeIoc  \
0                            http%3A%2F%2F104.248.196.145%2Fapache2   
1                           http%3A%2F%2Fajaraheritage.ge%2Fg7cberv   
2                  http%3A%2F%2Fcic-integration.com%2Fhjy93JNBasdas   
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
6  f8a7135496fd6168df5f0ea21c745db89ecea9accc29c5cf281cdf3145865092   
7                                  cc2db822f652ca67038ba7cca8a8bde3   
8                                                  ajaraheritage.ge   
0                                                                     
3                                                       51.75.29.61   
4                                                       33.44.55.66   
5                                                    52.183.120.194   
0                                    http://104.248.196.145/apache2   
1                                   http://ajaraheritage.ge/g7cberv   
2                          http://cic-integration.com/hjy93JNBasdas   
3      

## Browsing TI Results
To make it easier to walk through the returned results there is a browser. 
This shows you results aggregated by the IoC value (e.g. an individual IP 
Address or URL) for all providers.

For each provider that returns a result for an IoC, the summarized details 
will be shown in a table below the browse list.
Click on `Raw results from provider...` to see all returned data.

> **Note**: the reference URL may not work if you have not authenticated
> to the service

The value of the selected IoC entry is available as `ti_selector.value`

You can match this back to the original results DataFrame as follows:
```
results[results["Ioc"] == ti_selector.value[0]]
```

In [31]:
from msticpy.nbtools.ti_browser import browse_results
ti_selector = browse_results(data=results, height="200px")
ti_selector

## Specifying Time Ranges
Some providers (currently only AzSTI) support time ranges so that you can specify specific periods to search for.

If a provider does not support time ranges, the parameters will be ignored

In [ ]:
from datetime import datetime
search_origin = datetime(2019, 8, 5)
q_times = nbwidgets.QueryTime(units="hour", auto_display=True, origin_time=search_origin, max_after=24, max_before=24)

In [ ]:
# Using this data range returned no results
ti_lookup.lookup_iocs(data=ioc_ips, providers="AzSTI", start=q_times.start, end=q_times.end).head()

In [ ]:
from datetime import datetime
search_origin = datetime(2019, 8, 5)
q_times = nbwidgets.QueryTime(units="day", auto_display=True, origin_time=search_origin, max_after=24, max_before=24)

In [ ]:
# Using a wider ranges produces results
ti_lookup.lookup_iocs(data=ioc_ips, providers="AzSTI", start=q_times.start, end=q_times.end)